# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [41]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests
import json
import numpy as np
import gmaps

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geokey

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv('../Vacation_Search/WeatherPy_vacation.csv')

# Display sample data
vacation_df.head(10)

City_ID                    City Country  Max_Temp      Description  \
0        1    Vila Franca Do Campo      PT     66.61    broken clouds   
1       11                  Castro      BR     67.66  overcast clouds   
2       12                Necochea      AR     69.96  overcast clouds   
3       24            Ballitoville      ZA     73.54       light rain   
4       33                     Sur      OM     72.93       light rain   
5       38            Puerto Ayora      EC     69.55    broken clouds   
6       42                    Chuy      UY     66.83        clear sky   
7       51            Vila Do Maio      CV     74.19        clear sky   
8       57  Felipe Carrillo Puerto      MX     69.75       light rain   
9       58          Port Elizabeth      ZA     71.10             mist   

       Lat      Lng                            Hotel Name  
0  37.7167 -25.4333             Vinha d'Areia Beach Hotel  
1 -24.7911 -50.0119                  Hotel Central Palace  
2 -38.5473 -58.7368                   Cabañas Río Quequén  
3 -29.5390  31.2144               The Vineyard On Ballito  
4  22.5667  59.5289                             Sur Hotel  
5  -0.7393 -90.3518  Hostal La Mirada De Solitario George  
6 -33.6971 -53.4616                               Alerces  
7  15.1333 -23.2167           Residencial Jardins De Maio  
8  19.5833 -88.0500                      Hotel María José  
9 -33.9180  25.5701                       Waterford Hotel

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [3]:
# Configure the map plot
hotel_map = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Hotel Name", "Country","Description"]
)

# Display the map
hotel_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Hotel Name,Country,Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [9]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[vacation_df["City"] ==  "Cape Town"]
vacation_end = vacation_df.loc[vacation_df["City"] ==  "Port Elizabeth"]
vacation_stop1 = vacation_df.loc[vacation_df["City"] ==  "Richards Bay"]
vacation_stop2 = vacation_df.loc[vacation_df["City"] ==  "Bloemhof"]
vacation_stop3 = vacation_df.loc[vacation_df["City"] ==  "Bredasdorp"]



City_ID          City Country  Max_Temp      Description     Lat  \
122      631  Richards Bay      ZA      72.0  overcast clouds -28.783   

         Lng    Hotel Name  
122  32.0377  Protea Hotel

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [10]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df = pd.concat([vacation_start,vacation_stop1,vacation_stop2,vacation_stop3,vacation_end]).reset_index()
# Display sample data
itinerary_df.head()

index  City_ID            City Country  Max_Temp      Description      Lat  \
0     11       65       Cape Town      ZA     72.37        clear sky -33.9258   
1    122      631    Richards Bay      ZA     72.00  overcast clouds -28.7830   
2     98      522        Bloemhof      ZA     68.13    broken clouds -27.6469   
3     12       69      Bredasdorp      ZA     66.34  overcast clouds -34.5322   
4      9       58  Port Elizabeth      ZA     71.10             mist -33.9180   

       Lng       Hotel Name  
0  18.4232  Townhouse Hotel  
1  32.0377     Protea Hotel  
2  25.6070          Calimyn  
3  20.0403   Victoria Hotel  
4  25.5701  Waterford Hotel

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [26]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[["Lat","Lng","City"]].copy()

# Display sample data
waypoints_df

Lat      Lng            City
0 -33.9258  18.4232       Cape Town
1 -28.7830  32.0377    Richards Bay
2 -27.6469  25.6070        Bloemhof
3 -34.5322  20.0403      Bredasdorp
4 -33.9180  25.5701  Port Elizabeth

## Use GeoViews to create map that shows the four cities in the itinerary

In [12]:
# Configure the map plot by using the itineraty_df
waypoints_map = hotel_map = waypoints_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max_Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Hotel Name", "Country"]
)


In [38]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [14]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geokey,
}

In [15]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': '97b63ffc661f40c39a00762d069aa5d7',
 'waypoints': '-33.9258,18.4232|-28.783,32.0377|-27.6469,25.607|-34.5322,20.0403|-33.918,25.5701'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [16]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url,params=params)

# Convert the API response to JSON format
route_response = route_response.json()

print(json.dumps(route_response, indent=4, separators=(". ", " = ")))


{
    "features" = [
        {
            "type" = "Feature". 
            "properties" = {
                "mode" = "drive". 
                "waypoints" = [
                    {
                        "location" = [
                            18.4232. 
                            -33.9258
                        ]. 
                        "original_index" = 0
                    }. 
                    {
                        "location" = [
                            32.0377. 
                            -28.783
                        ]. 
                        "original_index" = 1
                    }. 
                    {
                        "location" = [
                            25.607. 
                            -27.6469
                        ]. 
                        "original_index" = 2
                    }. 
                    {
                        "location" = [
                            20.0403. 
                            -34.5322
       

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [17]:
legs = route_response['properties']['waypoints']
legs

[{'lat': -33.9258, 'lon': 18.4232},
 {'lat': -28.783, 'lon': 32.0377},
 {'lat': -27.6469, 'lon': 25.607},
 {'lat': -34.5322, 'lon': 20.0403},
 {'lat': -33.918, 'lon': 25.5701}]

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [21]:
# Create and empty list to store the longitude of each step
lng = []

# Create and empty list to store the latitude of step
lat =[]

# Loop through the legs coordinates to fetch the latitude and longitude for each step


SyntaxError: invalid syntax (1992274596.py, line 8)

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [32]:
# Create an empty DataFrame to store the steps' coordinates


# Add the steps' longitude and latitude from each step as columns to the DataFrame
start_city = waypoints_df.loc[waypoints_df["City"]=="Cape Town"]
first_city = waypoints_df.loc[waypoints_df["City"]=="Richards Bay"]
second_city = waypoints_df.loc[waypoints_df["City"]=="Bloemhof"]
third_city = waypoints_df.loc[waypoints_df["City"]=="Bredasdorp"]
end_city = waypoints_df.loc[waypoints_df["City"]=="Port Elizabeth"]

start = start_city["Lat"].to_numpy()[0], start_city["Lng"].to_numpy()[0]
first = first_city["Lat"].to_numpy()[0], first_city["Lng"].to_numpy()[0]
second = second_city["Lat"].to_numpy()[0], second_city["Lng"].to_numpy()[0]
third = second_city["Lat"].to_numpy()[0], second_city["Lng"].to_numpy()[0]
end = end_city["Lat"].to_numpy()[0], end_city["Lng"].to_numpy()[0]

# Display sample data
print(start,first,second,third,end)


(-33.9258, 18.4232) (-28.783, 32.0377) (-27.6469, 25.607) (-27.6469, 25.607) (-33.918, 25.5701)


##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [36]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(start,first,end)

ValueError: Dimensions specified as a tuple must be a tuple consisting of the name and label not: (-28.783, 32.0377)

In [42]:
fig = gmaps.figure()
city_itinerary = gmaps.directions_layer(
        start, end, waypoints=[first, second, third],
        travel_mode='DRIVING')

fig.add_layer(city_itinerary)
fig


Figure(layout=FigureLayout(height='420px'))